In [35]:

import sys
from pathlib import Path
root = Path.cwd()
import pandas as pd
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, roc_auc_score
from optuna import trial

if (root / "utils").exists():
    project_root = root
elif (root.parent / "utils").exists():
    project_root = root.parent

sys.path.insert(0, str(project_root))

from utils.data_preprocessing import (
    map_pistol_rounds,
    encode_categorical_columns
)
from utils.model_helpers import (
    train_lightgbm_model,
    model_traininng_pipeline

)

DROP_COLUMNS = ["demo_file", "tick", "user_name", "attacker_name"]
CATEGORICAL_COLS = ["weapon","attacker_team_name","user_team_name","map"]
TARGET_COL = "t_won_round"

In [2]:
df = pd.read_csv("../../data/data/processed_demo.csv")

In [3]:
display(df.head())

demo_file  tick  round  attacker_X  \
0  ../../data/demos/hotu-vs-betboom-m1-anubis.dem  2764      1   113.98847   
1  ../../data/demos/hotu-vs-betboom-m1-anubis.dem  3399      1  -130.49720   
2  ../../data/demos/hotu-vs-betboom-m1-anubis.dem  4109      1   128.15846   
3  ../../data/demos/hotu-vs-betboom-m1-anubis.dem  4132      1  -999.72920   
4  ../../data/demos/hotu-vs-betboom-m1-anubis.dem  4195      1  -896.42600   

   attacker_Y  attacker_Z attacker_name     user_X     user_Y     user_Z  ...  \
0   1605.7070  -31.968750   dukefissura  299.37762   712.1215 -28.968750  ...   
1   1820.2451   27.031250         S1ren -487.00037  2119.1350  18.683817  ...   
2   1279.7332  -31.952576       Boombl4  306.31857  1133.8534 -28.968750  ...   
3   1536.6414  -30.968750       n0rb3r7 -861.16860  1614.4656 -30.968750  ...   
4   1557.8730  -30.968750       n0rb3r7 -821.14820  1761.1349  43.203125  ...   

         weapon bomb_site  is_bomb_planted  round_time_left  \
0  usp_silencer         0                0            100.0   
1         glock         0                0             90.0   
2         glock         0                0             79.0   
3         elite         0                0             78.0   
4         elite         0                0             77.0   

   attacker_alive_count  user_alive_count  attacker_team_name user_team_name  \
0                     4                 4                  CT              T   
1                     3                 4                   T             CT   
2                     3                 3                   T             CT   
3                     2                 3                  CT              T   
4                     2                 2                  CT              T   

  t_won_round        map  
0           0  de_anubis  
1           0  de_anubis  
2           0  de_anubis  
3           0  de_anubis  
4           0  de_anubis  

[5 rows x 21 columns]

In [4]:
df.drop(columns=DROP_COLUMNS, inplace=True)

In [5]:
df = map_pistol_rounds(df)

In [6]:
display(df)


round  attacker_X  attacker_Y  attacker_Z      user_X     user_Y  \
0        1   113.98847   1605.7070  -31.968750   299.37762   712.1215   
1        1  -130.49720   1820.2451   27.031250  -487.00037  2119.1350   
2        1   128.15846   1279.7332  -31.952576   306.31857  1133.8534   
3        1  -999.72920   1536.6414  -30.968750  -861.16860  1614.4656   
4        1  -896.42600   1557.8730  -30.968750  -821.14820  1761.1349   
..     ...         ...         ...         ...         ...        ...   
628     24  -995.39136  -1337.7007 -161.841550   179.97043 -2343.2722   
629     24  -767.96454  -1678.9241 -173.461000   174.63446 -1667.9617   
630     24  -827.38500  -2293.9255 -174.426570  -523.15753 -1362.5345   
631     24  -799.72780  -2297.8400 -176.711000  -721.74540 -1531.3291   
632     24    74.83341  -2095.0112  -39.968750 -1194.18590 -1259.9813   

         user_Z         weapon  bomb_site  is_bomb_planted  round_time_left  \
0    -28.968750   usp_silencer          0                0            100.0   
1     18.683817          glock          0                0             90.0   
2    -28.968750          glock          0                0             79.0   
3    -30.968750          elite          0                0             78.0   
4     43.203125          elite          0                0             77.0   
..          ...            ...        ...              ...              ...   
628  -39.968750            awp          0                0             34.0   
629 -167.968750  m4a1_silencer          0                0             33.0   
630 -138.732360           ak47          0                0             31.0   
631 -167.968750           ak47          0                0             30.0   
632 -167.968750           ak47          0                0             17.0   

     attacker_alive_count  user_alive_count attacker_team_name user_team_name  \
0                       4                 4                 CT              T   
1                       3                 4                  T             CT   
2                       3                 3                  T             CT   
3                       2                 3                 CT              T   
4                       2                 2                 CT              T   
..                    ...               ...                ...            ...   
628                     2                 2                 CT              T   
629                     2                 1                 CT              T   
630                     0                 2                  T             CT   
631                     0                 1                  T             CT   
632                     0                 0                  T             CT   

     t_won_round        map  is_pistol_round  
0              0  de_anubis                1  
1              0  de_anubis                1  
2              0  de_anubis                1  
3              0  de_anubis                1  
4              0  de_anubis                1  
..           ...        ...              ...  
628            1  de_mirage                0  
629            1  de_mirage                0  
630            1  de_mirage                0  
631            1  de_mirage                0  
632            1  de_mirage                0  

[633 rows x 18 columns]

In [7]:
df = encode_categorical_columns(df, CATEGORICAL_COLS)[0].drop(columns=["round"])

In [8]:
display(df)

attacker_X  attacker_Y  attacker_Z      user_X     user_Y      user_Z  \
0     113.98847   1605.7070  -31.968750   299.37762   712.1215  -28.968750   
1    -130.49720   1820.2451   27.031250  -487.00037  2119.1350   18.683817   
2     128.15846   1279.7332  -31.952576   306.31857  1133.8534  -28.968750   
3    -999.72920   1536.6414  -30.968750  -861.16860  1614.4656  -30.968750   
4    -896.42600   1557.8730  -30.968750  -821.14820  1761.1349   43.203125   
..          ...         ...         ...         ...        ...         ...   
628  -995.39136  -1337.7007 -161.841550   179.97043 -2343.2722  -39.968750   
629  -767.96454  -1678.9241 -173.461000   174.63446 -1667.9617 -167.968750   
630  -827.38500  -2293.9255 -174.426570  -523.15753 -1362.5345 -138.732360   
631  -799.72780  -2297.8400 -176.711000  -721.74540 -1531.3291 -167.968750   
632    74.83341  -2095.0112  -39.968750 -1194.18590 -1259.9813 -167.968750   

     weapon  bomb_site  is_bomb_planted  round_time_left  \
0        19          0                0            100.0   
1         7          0                0             90.0   
2         7          0                0             79.0   
3         3          0                0             78.0   
4         3          0                0             77.0   
..      ...        ...              ...              ...   
628       1          0                0             34.0   
629      11          0                0             33.0   
630       0          0                0             31.0   
631       0          0                0             30.0   
632       0          0                0             17.0   

     attacker_alive_count  user_alive_count  attacker_team_name  \
0                       4                 4                   0   
1                       3                 4                   1   
2                       3                 3                   1   
3                       2                 3                   0   
4                       2                 2                   0   
..                    ...               ...                 ...   
628                     2                 2                   0   
629                     2                 1                   0   
630                     0                 2                   1   
631                     0                 1                   1   
632                     0                 0                   1   

     user_team_name  t_won_round  map  is_pistol_round  
0                 1            0    0                1  
1                 0            0    0                1  
2                 0            0    0                1  
3                 1            0    0                1  
4                 1            0    0                1  
..              ...          ...  ...              ...  
628               1            1    2                0  
629               1            1    2                0  
630               0            1    2                0  
631               0            1    2                0  
632               0            1    2                0  

[633 rows x 17 columns]

In [9]:
X_train, X_val, y_train, y_val = train_test_split(df.drop(columns="t_won_round"),df["t_won_round"],test_size=0.2)

In [10]:
display(X_train)

attacker_X  attacker_Y  attacker_Z      user_X      user_Y      user_Z  \
352  -706.33136 -2323.26950 -178.003780  -776.76850 -1311.30970 -167.968750   
98   -714.35190  -682.51514  106.031265 -1879.13110   175.21478   58.031250   
509  -797.30554 -1376.39710 -167.968750  -786.53650 -2242.55200 -179.968750   
529 -2041.41110   654.40186  -43.968750 -1248.04330   486.49146 -163.678710   
284  1314.65110  2503.56050   70.239090   489.78006  2099.27100  104.078125   
..          ...         ...         ...         ...         ...         ...   
281   416.30356  2584.96530   95.498764   604.43164  2376.71000   67.031250   
474 -1419.11630   162.18160 -167.968750 -2250.16330  -129.57672 -167.827880   
562 -1879.52090   742.44500  -47.968750 -2257.16600   789.77136 -125.556580   
94   -788.34900   229.31868  -68.416626  -583.32730    63.29404  -93.968750   
578 -1260.20290   404.65503 -167.968750 -1853.99170   681.77410  -47.968750   

     weapon  bomb_site  is_bomb_planted  round_time_left  \
352       0          1                0             50.0   
98       14          0                0             32.0   
509      11          1                1             35.0   
529       0          2                0             88.0   
284      11          1                0             78.0   
..      ...        ...              ...              ...   
281       0          0                0             27.0   
474       0          2                0             44.0   
562       7          2                0             64.0   
94        4          0                0             84.0   
578       1          0                0             34.0   

     attacker_alive_count  user_alive_count  attacker_team_name  \
352                     2                 4                   0   
98                      3                 0                   0   
509                     0                 0                   0   
529                     4                 3                   1   
284                     3                 4                   0   
..                    ...               ...                 ...   
281                     0                 4                   1   
474                     4                 3                   1   
562                     3                 2                   1   
94                      4                 3                   0   
578                     4                 2                   0   

     user_team_name  map  is_pistol_round  
352               1    2                0  
98                1    0                0  
509               1    2                0  
529               0    2                0  
284               1    1                0  
..              ...  ...              ...  
281               0    1                0  
474               0    2                0  
562               0    2                1  
94                1    0                0  
578               1    2                0  

[506 rows x 16 columns]

In [11]:
display(y_train)

352    1
98     0
509    0
529    1
284    1
      ..
281    0
474    1
562    1
94     0
578    0
Name: t_won_round, Length: 506, dtype: int64

In [48]:
def create_parameter_space(trial):
    """Create custom parameter space for LightGBM hyperparameter optimization."""
    param_grid = {
        "n_estimators": trial.suggest_int("n_estimators",50,1000,step = 5),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
        "num_leaves": trial.suggest_int("num_leaves", 15, 3000, step=5),
        "max_depth": trial.suggest_int("max_depth", 2, 12),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 20, 100, step=5),
        "max_bin": trial.suggest_int("max_bin", 20, 300),
        "lambda_l1": trial.suggest_float("lambda_l1", 0, 0.8, step=0.02),
        "lambda_l2": trial.suggest_float("lambda_l2", 0, 0.8, step=0.02),
        "min_gain_to_split": trial.suggest_float("min_gain_to_split", 0, 15),
        "bagging_fraction": trial.suggest_float(
            "bagging_fraction", 0.2, 0.95, step=0.1
        ),
        "feature_fraction": trial.suggest_float(
            "feature_fraction", 0.2, 0.95, step=0.1
        ),
    }
    return param_grid


In [49]:
model, metrics = model_traininng_pipeline(
    X_train, 
    y_train, 
    X_val, 
    y_val, 
    parameter_space=create_parameter_space,
    n_trials=10,
    metric="balanced_accuracy"
)


[I 2026-01-31 15:56:47,469] A new study created in memory with name: no-name-3fe4b4ec-b7e3-49e9-a701-73733980c09d
c:\Users\mikko\projects\cs-win-model\.venv\Lib\site-packages\optuna\distributions.py:671: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced with [0.2, 0.9].
  optuna_warn(
[I 2026-01-31 15:56:47,604] Trial 0 finished with value: 0.7776511180992314 and parameters: {'n_estimators': 405, 'learning_rate': 0.28570714885887566, 'num_leaves': 2200, 'max_depth': 8, 'min_data_in_leaf': 30, 'max_bin': 63, 'lambda_l1': 0.04, 'lambda_l2': 0.7000000000000001, 'min_gain_to_split': 9.016725176148132, 'bagging_fraction': 0.7, 'feature_fraction': 0.2}. Best is trial 0 with value: 0.7776511180992314.
c:\Users\mikko\projects\cs-win-model\.venv\Lib\site-packages\optuna\distributions.py:671: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will 

[LightGBM] [Warning] min_data_in_leaf is set=30, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=30
[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2
[LightGBM] [Warning] min_gain_to_split is set=9.016725176148132, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=9.016725176148132
[LightGBM] [Warning] lambda_l1 is set=0.04, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.04
[LightGBM] [Warning] lambda_l2 is set=0.7000000000000001, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.7000000000000001
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7
[LightGBM] [Warning] min_data_in_leaf is set=30, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=30
[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2


[I 2026-01-31 15:56:47,798] Trial 1 finished with value: 0.7730913696715584 and parameters: {'n_estimators': 975, 'learning_rate': 0.2514083658321223, 'num_leaves': 645, 'max_depth': 4, 'min_data_in_leaf': 35, 'max_bin': 105, 'lambda_l1': 0.42, 'lambda_l2': 0.34, 'min_gain_to_split': 4.368437102970629, 'bagging_fraction': 0.6000000000000001, 'feature_fraction': 0.30000000000000004}. Best is trial 1 with value: 0.7730913696715584.
c:\Users\mikko\projects\cs-win-model\.venv\Lib\site-packages\optuna\distributions.py:671: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced with [0.2, 0.9].
  optuna_warn(


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped t

[I 2026-01-31 15:56:47,891] Trial 2 finished with value: 0.7776511180992314 and parameters: {'n_estimators': 325, 'learning_rate': 0.11624493455517058, 'num_leaves': 1375, 'max_depth': 10, 'min_data_in_leaf': 35, 'max_bin': 164, 'lambda_l1': 0.48, 'lambda_l2': 0.02, 'min_gain_to_split': 9.113172778521575, 'bagging_fraction': 0.30000000000000004, 'feature_fraction': 0.2}. Best is trial 1 with value: 0.7730913696715584.
c:\Users\mikko\projects\cs-win-model\.venv\Lib\site-packages\optuna\distributions.py:671: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced with [0.2, 0.9].
  optuna_warn(


...

[LightGBM] [Warning] min_data_in_leaf is set=45, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=45
[LightGBM] [Warning] feature_fraction is set=0.6000000000000001, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6000000000000001
[LightGBM] [Warning] min_gain_to_split is set=5.3512999004038395, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=5.3512999004038395
[LightGBM] [Warning] lambda_l1 is set=0.22, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.22
[LightGBM] [Warning] lambda_l2 is set=0.66, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.66
[LightGBM] [Warning] bagging_fraction is set=0.4, subsample=1.0 will be ignored. Current value: bagging_fraction=0.4
[LightGBM] [Warning] min_data_in_leaf is set=85, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=85
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=

c:\Users\mikko\projects\cs-win-model\.venv\Lib\site-packages\optuna\distributions.py:671: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced with [0.2, 0.9].
  optuna_warn(
[I 2026-01-31 15:56:48,832] Trial 8 finished with value: 0.7776511180992314 and parameters: {'n_estimators': 895, 'learning_rate': 0.1469423282969653, 'num_leaves': 370, 'max_depth': 9, 'min_data_in_leaf': 80, 'max_bin': 177, 'lambda_l1': 0.62, 'lambda_l2': 0.4, 'min_gain_to_split': 7.840992440729911, 'bagging_fraction': 0.5, 'feature_fraction': 0.2}. Best is trial 4 with value: 0.7532538434661076.
c:\Users\mikko\projects\cs-win-model\.venv\Lib\site-packages\optuna\distributions.py:671: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced with [0.2, 0.9].
  optuna_warn(


[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[

[I 2026-01-31 15:56:48,923] Trial 9 finished with value: 0.7658586652690426 and parameters: {'n_estimators': 150, 'learning_rate': 0.019114463849152934, 'num_leaves': 1915, 'max_depth': 5, 'min_data_in_leaf': 60, 'max_bin': 275, 'lambda_l1': 0.2, 'lambda_l2': 0.32, 'min_gain_to_split': 11.333267078145731, 'bagging_fraction': 0.30000000000000004, 'feature_fraction': 0.2}. Best is trial 4 with value: 0.7532538434661076.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Stopped training because there are no 

In [50]:
def metrics_to_df(metrics:dict) -> pd.DataFrame:
    df = pd.DataFrame.from_dict(metrics["classification_report"])
    df["auc"] = metrics["auc"]
    return df


In [51]:
df_metrics = metrics_to_df(metrics)

In [52]:
display(df_metrics)

0          1  accuracy   macro avg  weighted avg       auc
precision   0.657143   0.824561  0.732283    0.740852      0.750739  0.848089
recall      0.821429   0.661972  0.732283    0.741700      0.732283  0.848089
f1-score    0.730159   0.734375  0.732283    0.732267      0.732516  0.848089
support    56.000000  71.000000  0.732283  127.000000    127.000000  0.848089

In [53]:
model.predict(X_val)

[LightGBM] [Warning] min_data_in_leaf is set=65, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=65
[LightGBM] [Warning] feature_fraction is set=0.6000000000000001, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6000000000000001
[LightGBM] [Warning] min_gain_to_split is set=14.092484123462837, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=14.092484123462837
[LightGBM] [Warning] lambda_l1 is set=0.78, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.78
[LightGBM] [Warning] lambda_l2 is set=0.62, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.62
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9


array([0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 0, 0, 1, 0,
       0, 1, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0,
       0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 0,
       1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0,
       0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0])

In [54]:
test_model = lgb.LGBMClassifier()
test_model.fit(X_train, y_train)
test_model.predict(X_val)

[LightGBM] [Info] Number of positive: 266, number of negative: 240
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000091 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1122
[LightGBM] [Info] Number of data points in the train set: 506, number of used features: 16
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.525692 -> initscore=0.102857
[LightGBM] [Info] Start training from score 0.102857
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

array([1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 1, 1,
       1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0,
       0, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0,
       1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0,
       0, 1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 0, 1,
       0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0])

In [55]:
test_preds = test_model.predict(X_val)

In [56]:
print(classification_report(y_val, test_preds))

              precision    recall  f1-score   support

           0       0.74      0.75      0.74        56
           1       0.80      0.79      0.79        71

    accuracy                           0.77       127
   macro avg       0.77      0.77      0.77       127
weighted avg       0.77      0.77      0.77       127



In [57]:
display(df_metrics)

0          1  accuracy   macro avg  weighted avg       auc
precision   0.657143   0.824561  0.732283    0.740852      0.750739  0.848089
recall      0.821429   0.661972  0.732283    0.741700      0.732283  0.848089
f1-score    0.730159   0.734375  0.732283    0.732267      0.732516  0.848089
support    56.000000  71.000000  0.732283  127.000000    127.000000  0.848089

In [33]:
pred_proba =test_model.predict_proba(X_val)

In [36]:
test_auc = roc_auc_score(y_val, pred_proba[:, 1])

In [37]:
print(test_auc)

0.8606639839034205
